In [53]:
import sys, os

print(sys.executable)
# insert '/home/bussotti/AB/code XFC' in the path
path = '/homes/bussotti/XFC2/code'
save_path = '/homes/bussotti/feverous_work/feverousdata/AB/plots'

for extension in ['pdf', 'html', 'svg']:
    os.makedirs(os.path.join(save_path, extension), exist_ok=True)

if path not in sys.path:
    sys.path.insert(0, path)

sys.path.insert(0, "/homes/bussotti/feverous_work/feverousdata/feverous/")

/home/bussotti/.conda/envs/feverous2/bin/python3


In [54]:
# get name of current environment with conda
!pwd

/homes/bussotti


In [55]:
import pandas as pd
import os
%matplotlib inline
import plotly.express as px
# set color-schema with white background
import plotly.io as pio

# check if in a colaboratory environment
if 'google.colab' in sys.modules:
    pio.renderers.default = 'colab'
import plotly.graph_objs as go

ratio = 4 / 3
pixel_width = 1000
pixel_height = pixel_width / ratio

pio.templates["google"] = go.layout.Template(
    layout_colorway=['#4285F4', '#DB4437', '#F4B400', '#0F9D58',
                     '#185ABC', '#B31412', '#EA8600', '#137333',
                     '#d2e3fc', '#ceead6']
)
# new template with matplotlib color schema for plotly
pio.templates["matplotlib"] = go.layout.Template(
    layout_colorway=['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728',
                     '#9467bd', '#8c564b', '#e377c2', '#7f7f7f',
                     '#bcbd22', '#17becf']
)

layout = go.Layout(
    autosize=False,
    width=pixel_width,
    height=pixel_height,
    margin=go.layout.Margin(
        l=50,
        r=50,
        b=100,
        t=100,
        pad=4
    ),
)
layout_dict = dict(autosize=False,
                   width=pixel_width,
                   height=pixel_height,
                   margin=go.layout.Margin(
                       l=50,
                       r=50,
                       b=100,
                       t=100,
                       pad=4
                   )
                   )
h_legend_dict = dict(legend=dict(
    orientation="h",
    yanchor="bottom",
    y=1.02,
    xanchor="right",
    x=1
))
pio.templates.default = "matplotlib"

pio.kaleido.scope.chromium_args = tuple([
    arg for arg in pio.kaleido.scope.chromium_args if arg != "--disable-dev-shm-usage"
])


def save_fig(fig, name, save_path=save_path):
    fig.write_html(os.path.join(save_path, 'html', name + '.html'))
    fig.write_image(os.path.join(save_path, 'svg', name + '.svg'))
    # fig.write_image(os.path.join(save_path, 'pdf', name + '.pdf'))

In [56]:
import explainable_fact_checking as xfc

files_dict = xfc.explanations_load.load_explanations_lime(dir='/homes/bussotti/feverous_work/feverousdata/AB/')
files_dict.keys()

dict_keys(['plots', 'tmp_predictions', 'lime_explanations_AB', 'test_folder', 'explanations', 'tmp', '.ipynb_checkpoints', 'lime_explanations'])

In [57]:
# from explainable_fact_checking import style_exp_to_html
# 
# files_dict['feverous_dev_challenges_sentencesandtable.jsonl']
# # render html of the first explanation converted with style_exp_to_html
# file_keys = list(files_dict.keys())
# exp_dict = files_dict[file_keys[0]]
# exp_keys = list(exp_dict.keys())
# 
# html_code = style_exp_to_html(exp_dict[exp_keys[4]])
# # render html code in notebook
# from IPython.display import HTML
# 
# HTML(html_code)

In [58]:

# explanation_df = load_explanations_lime_to_df(dir='/homes/bussotti/feverous_work/feverousdata/AB/')

# or load './AB/explanations_lime.csv'
explanation_df = pd.read_csv('/homes/bussotti/feverous_work/feverousdata/AB/explanations_lime.csv')

explanation_df.groupby('filename')['id'].nunique()

filename
ex_AB_00                 7
feverous_dev_SO_01    1000
feverous_dev_ST_01    1000
original_TO_01        1000
Name: id, dtype: int64

In [59]:
# get example of id 7389 and file 'feverous_dev_ST_01_pred_only_claim.json'
explanation_df[
    (explanation_df['id'] == 7389) & (explanation_df['filename'] == 'feverous_dev_ST_01_pred_only_claim.json')]

Empty DataFrame
Columns: [id, type, unit_text, unit_index, SUPPORTS, REFUTES, NOT ENOUGH INFO, filename, num_samples, label, execution_time, local_pred, NOT ENOUGH INFO_predict_proba, SUPPORTS_predict_proba, REFUTES_predict_proba, predicted_label, score_on_predicted_label]
Index: []

In [60]:
no_claim_mask = explanation_df['type'].str.contains('evidence')

In [61]:
# histogram of unit_index with plotly without considering the type 'claim'
import plotly.figure_factory as ff

id_cols = ['id', 'filename']
tdf = explanation_df[no_claim_mask]
gdf = tdf.groupby(id_cols, as_index=False).size()
# fig = px.histogram(gdf, x='size', title='Histogram of number of evidence per claim',
#                    labels={'size': 'n evidence', 'value': 'percentage'},
#                    color='filename',
#                    hover_data=gdf.columns,
#                    # set color trasparency
#                    #   color_discrete_sequence=['rgba(0,0,0,0.5)']
#                    
#                    )

pivot = gdf.pivot(index='id', columns='filename', values='size')
fig = ff.create_distplot([pivot[col].dropna().values for col in pivot.columns],
                         pivot.columns, show_hist=True, show_rug=False,
                         )

fig.update_layout(**layout_dict, **h_legend_dict
                  )
# annotate the cumulative percentage of the unit_index only 1 decimal digits
# fig.update_traces(textposition='outside', text=gdf.value_counts(normalize=True).sort_index().values * 100,
#                   texttemplate='%{text:.1f}', textfont_size=10)

fig.update_xaxes(tick0=1, dtick=2)

fig.show()

save_fig(fig, '00-histogram_n_unit')

In [62]:
evidence_mask = explanation_df['type'] == 'evidence'
ground_truth = explanation_df[evidence_mask].groupby(id_cols).head(1)['label'].value_counts(normalize=True)
ground_truth.name = 'ground_truth'

In [63]:
predicted = explanation_df[evidence_mask].groupby(id_cols).head(1)['predicted_label'].value_counts(normalize=True)
predicted.name = 'predicted_label'

In [64]:
only_claim_mask = explanation_df['type'] == 'only_claim'
only_claim = explanation_df.loc[only_claim_mask, xfc.xfc_utils.class_names].idxmax(1).value_counts(normalize=True)
only_claim.name = 'only_claim'


In [65]:
label_stats = pd.concat([ground_truth, predicted, only_claim], axis=1)
fig = px.bar(label_stats, title='Distribution of labels over the evidence set',
             #non stacked
             barmode='group',)
fig.update_layout(**layout_dict, **h_legend_dict)
fig.show()

In [77]:
value_col = xfc.xfc_utils.class_names[2]
pivot = explanation_df.pivot(index=id_cols + ['unit_index'], columns='type', values=value_col)
display(pivot.describe())
fig = ff.create_distplot([pivot[col].dropna().values for col in pivot.columns],
                         pivot.columns, show_hist=True, show_rug=False, show_curve=True,
                         histnorm='probability density',
                         bin_size=0.01

                         )

fig.update_layout(**layout_dict, **h_legend_dict)
# add title
fig.update_layout(title=f'Distribution of {value_col} over the evidence set')

fig.show()

type   claim_intercept      evidence   only_claim
count      3007.000000  12882.000000  3007.000000
mean          0.827849     -0.056080     0.924945
std           0.310986      0.202447     0.161731
min          -0.216809     -1.059833     0.021168
25%           0.664984     -0.087434     0.951056
50%           0.966575     -0.000688     0.985576
75%           0.997982      0.008960     0.994015
max           1.524574      0.922999     0.999274

In [78]:
# boxplot of ['NOT ENOUGH INFO', 'SUPPORTS', 'REFUTES'] segmented by predicted_label and filename. hue on type

for value_col in xfc.xfc_utils.class_names[1:]:
    fig = px.box(explanation_df, x='predicted_label', y=[value_col],
                 title=f'Box plot of scores over class {value_col}',
                 labels={'predicted_label': 'predicted_label', 'value': 'quantiles'},
                 color='type',
                 category_orders={'predicted_label': xfc.xfc_utils.class_names},
                 # facet_col='filename',
                 )
    fig.update_layout(**layout_dict, **h_legend_dict)
    # save_fig(fig, f'01-boxplot_{value_col}')
    fig.show()
    

In [69]:
# filter filename 'ex_AB_00'
explanation_df[explanation_df['filename'] == 'ex_AB_00']

id             type                                          unit_text  \
0    4329         evidence  He reorganized the Clear Grit ([[Liberal_Party...   
1    4329  claim_intercept  George Brown began his Liberal Party leadershi...   
2    4329       only_claim  George Brown began his Liberal Party leadershi...   
3    5003         evidence  It is roughly a four-block by four-and-a-half-...   
4    5003  claim_intercept  Brookings University Residential Historic Dist...   
5    5003       only_claim  Brookings University Residential Historic Dist...   
6    6079         evidence  Alex Minsky is a retired [[United_States_Marin...   
7    6079         evidence  At the beginning of his first tour of [[Afghan...   
8    6079         evidence  After his brother died from a drug overdose, h...   
9    6079         evidence  It was during one of his routine workouts that...   
10   6079         evidence  However, his career didn't start to take off u...   
11   6079  claim_intercept  After his brother died from a drug overdose, A...   
12   6079       only_claim  After his brother died from a drug overdose, A...   
13   6473         evidence  The tournament is played at the [[Dasarath_Ran...   
14   6473         evidence  Ncell Cup is a [[Association_football|football...   
15   6473         evidence  The Ncell Cup tournament, sponsored by telecom...   
16   6473         evidence  In 2013 Rana won the most valuable player awar...   
17   6473         evidence  As a prize she was gifted one [[Yamaha_Motor_C...   
18   6473  claim_intercept  Sajana Raina was gifted a Yamaha scooter when ...   
19   6473       only_claim  Sajana Raina was gifted a Yamaha scooter when ...   
20   8406         evidence  On 27 February 2014, Seri received his first s...   
21   8406         evidence  On 17 November 2015, Seri scored a goal in the...   
22   8406         evidence  In January 2010, Seri started his career as a ...   
23   8406         evidence  On 31 August 2013, two months after finishing ...   
24   8406         evidence  On 11 June 2015, Seri officially joined [[Ligu...   
25   8406         evidence  On 8 August 2015, Seri made his competitive de...   
26   8406         evidence  On 27 September 2015, he scored in the 53rd mi...   
27   8406         evidence  In July 2018, Seri joined [[Fulham_F.C.|Fulham...   
28   8406         evidence  On 18 July 2019, Seri joined [[Galatasaray_S.K...   
29   8406         evidence  Seri made a total of three appearances for the...   
30   8406         evidence                                 Jean Michaël Seri   
31   8406         evidence                   Full name is Jean Michaël Seri.   
32   8406         evidence        Personal information is Jean Michaël Seri.   
33   8406         evidence        2010–2013 is [[ASEC_Mimosas|ASEC Mimosas]].   
34   8406         evidence  Senior career* is [[ASEC_Mimosas|ASEC Mimosas]...   
35   8406         evidence    2012–2013 is → [[F.C._Porto_B|Porto B]] (loan).   
36   8406         evidence  2013–2015 is [[F.C._Paços_de_Ferreira|Paços ...   
37   8406         evidence                    2015–2018 is [[OGC_Nice|Nice]].   
38   8406         evidence                   2018– is [[Fulham_F.C.|Fulham]].   
39   8406         evidence  2019–2020 is → [[Galatasaray_S.K._(football)|G...   
40   8406         evidence  2011 is [[Ivory_Coast_national_under-23_footba...   
41   8406         evidence  National team is [[Ivory_Coast_national_footba...   
42   8406         evidence  2015– is [[Ivory_Coast_national_football_team|...   
43   8406  claim_intercept  Jean Michaël Seri only play at local football ...   
44   8406       only_claim  Jean Michaël Seri only play at local football ...   
45  15275         evidence  In late 1987, prime minister [[Ingvar_Carlsson...   
46  15275         evidence  He wanted Lidbom to lead an investigation into...   
47  15275         evidence  This was prompted by the escape of convicted s...   
48  15275         evidence  Lidbom con

# Is the order affecting the impact of evidence?
# Is the claim more important than the evidence?

In [70]:
explanation_df[only_claim_mask]

id        type                                          unit_text  \
2       4329  only_claim  George Brown began his Liberal Party leadershi...   
5       5003  only_claim  Brookings University Residential Historic Dist...   
12      6079  only_claim  After his brother died from a drug overdose, A...   
19      6473  only_claim  Sajana Raina was gifted a Yamaha scooter when ...   
44      8406  only_claim  Jean Michaël Seri only play at local football ...   
...      ...         ...                                                ...   
18881  51676  only_claim  Radostin Radev is the mayor of Kostenets, a to...   
18884  52200  only_claim  Some of the notable professional wrestling eve...   
18888  52212  only_claim  During the 1949 season, under captain John Gil...   
18891  52216  only_claim  The X Boat, designed by John O. Johnson, a Nor...   
18895  52288  only_claim  List of power stations in Bahrain Madrid with ...   

       unit_index  SUPPORTS   REFUTES  NOT ENOUGH INFO        filename  \
2               0  0.011034  0.988920         0.000047        ex_AB_00   
5               0  0.014497  0.985450         0.000053        ex_AB_00   
12              0  0.001383  0.998583         0.000034        ex_AB_00   
19              0  0.013131  0.986828         0.000041        ex_AB_00   
44              0  0.004210  0.995751         0.000038        ex_AB_00   
...           ...       ...       ...              ...             ...   
18881           0  0.404441  0.595470         0.000089  original_TO_01   
18884           0  0.003176  0.996786         0.000038  original_TO_01   
18888           0  0.025378  0.974572         0.000050  original_TO_01   
18891           0  0.004041  0.995922         0.000037  original_TO_01   
18895           0  0.005258  0.994691         0.000051  original_TO_01   

       num_samples     label  execution_time  local_pred  \
2              NaN   REFUTES             NaN         NaN   
5              NaN   REFUTES             NaN         NaN   
12             NaN  SUPPORTS             NaN         NaN   
19             NaN  SUPPORTS             NaN         NaN   
44             NaN   REFUTES             NaN         NaN   
...            ...       ...             ...         ...   
18881          NaN  SUPPORTS             NaN         NaN   
18884          NaN   REFUTES             NaN         NaN   
18888          NaN   REFUTES             NaN         NaN   
18891          NaN   REFUTES             NaN         NaN   
18895          NaN   REFUTES             NaN         NaN   

       NOT ENOUGH INFO_predict_proba  SUPPORTS_predict_proba  \
2                           0.000033                0.001757   
5                           0.000054                0.004583   
12                          0.000047                0.992824   
19                          0.000055                0.993240   
44                          0.000028                0.001541   
...                              ...                     ...   
18881                       0.000088                0.998814   
18884                       0.000039                0.003215   
18888                       0.000038                0.001192   
18891                       0.000044                0.001158   
18895                       0.000048                0.001489   

       REFUTES_predict_proba predicted_label  score_on_predicted_label  
2                   0.998210         REFUTES                  0.988920  
5                   0.995363         REFUTES                  0.985450  
12                  0.007130        SUPPORTS                  0.001383  
19                  0.006705        SUPPORTS                  0.013131  
44                  0.998431         REFUTES                  0.995751  
...                      ...             ...                       ...  
18881               0.001098        SUPPORTS                  0.404441  
18884               0.996746         REFUTES                  0.996786  
18888               0.998

In [71]:
to_group = ['type', 'unit_index', 'predicted_label']

grouped_df = explanation_df.groupby(to_group)['score_on_predicted_label'].agg(
    ['mean', 'std', ('mean_ci', xfc.xfc_utils.mean_confidence_interval)]).reset_index()

for tpredicted_label in grouped_df['predicted_label'].unique():
    # fig = px.bar(grouped_df[grouped_df['predicted_label']==tdf], x=['type','unit_index'], y='mean', color='type', error_y='std',
    #              )
    # set the title as the predicted_label
    fig = px.bar(grouped_df[grouped_df['predicted_label'] == tpredicted_label], x='unit_index', y='mean', color='type',
                 error_y='mean_ci',
                 title=f'{tpredicted_label} mean and 95% confidence interval of score_on_predicted_label'
                 )

    # do not vertical stack the bars
    fig.update_layout(barmode='group',
                      **layout_dict, **h_legend_dict)
    save_fig(fig, f'01-{tpredicted_label}_mean_ci')
    fig.show()

# the same but with std as error bar, explain the chart in the title
for tpredicted_label in grouped_df['predicted_label'].unique():
    name = f'{tpredicted_label} mean and std of score_on_predicted_label'
    fig = px.bar(grouped_df[grouped_df['predicted_label'] == tpredicted_label], x='unit_index', y='mean', color='type',
                 error_y='std',
                 title=name
                 )
    fig.update_layout(barmode='group',
                      **layout_dict, **h_legend_dict)
    save_fig(fig, f'01-{tpredicted_label}_mean_std')
    fig.show()


/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide



In [72]:
explanation_df

id             type  \
0       4329         evidence   
1       4329  claim_intercept   
2       4329       only_claim   
3       5003         evidence   
4       5003  claim_intercept   
...      ...              ...   
18891  52216       only_claim   
18892  52288         evidence   
18893  52288         evidence   
18894  52288  claim_intercept   
18895  52288       only_claim   

                                               unit_text  unit_index  \
0      He reorganized the Clear Grit ([[Liberal_Party...           0   
1      George Brown began his Liberal Party leadershi...           0   
2      George Brown began his Liberal Party leadershi...           0   
3      It is roughly a four-block by four-and-a-half-...           0   
4      Brookings University Residential Historic Dist...           0   
...                                                  ...         ...   
18891  The X Boat, designed by John O. Johnson, a Nor...           0   
18892       List of power stations in Bahrain_cell_0_1_0           0   
18893       List of power stations in Bahrain_cell_0_1_2           1   
18894                                                NaN           0   
18895  List of power stations in Bahrain Madrid with ...           0   

       SUPPORTS   REFUTES  NOT ENOUGH INFO        filename  num_samples  \
0     -0.000148  0.000148    -2.111147e-07        ex_AB_00          NaN   
1      0.002052  0.997914     3.370811e-05        ex_AB_00          NaN   
2      0.011034  0.988920     4.655146e-05        ex_AB_00          NaN   
3     -0.000158  0.000158     1.981203e-08        ex_AB_00          NaN   
4      0.004898  0.995047     5.407040e-05        ex_AB_00          NaN   
...         ...       ...              ...             ...          ...   
18891  0.004041  0.995922     3.672142e-05  original_TO_01          NaN   
18892 -0.008725  0.008776    -5.070051e-05  original_TO_01        500.0   
18893  0.004724 -0.004757     3.246124e-05  original_TO_01        500.0   
18894  0.009885  0.990028     8.706735e-05  original_TO_01        500.0   
18895  0.005258  0.994691     5.129074e-05  original_TO_01          NaN   

         label  execution_time  local_pred  NOT ENOUGH INFO_predict_proba  \
0          NaN             NaN    0.998062                       0.000033   
1          NaN             NaN    0.998062                       0.000033   
2      REFUTES             NaN         NaN                       0.000033   
3          NaN             NaN    0.995205                       0.000054   
4          NaN             NaN    0.995205                       0.000054   
...        ...             ...         ...                            ...   
18891  REFUTES             NaN         NaN                       0.000044   
18892  REFUTES        6.628436    0.994046                       0.000048   
18893  REFUTES        6.628436    0.994046                       0.000048   
18894  REFUTES        6.628436    0.994046                       0.000048   
18895  REFUTES             NaN         NaN                       0.000048   

       SUPPORTS_predict_proba  REFUTES_predict_proba predicted_label  \
0                    0.001757               0.998210         REFUTES   
1                    0.001757               0.998210         REFUTES   
2                    0.001757               0.998210         REFUTES   
3                    0.004583               0.995363         REFUTES   
4                    0.004583               0.995363         REFUTES   
...                       ...                    ...             ...   
18891                0.001158               0.998798         REFUTES   
18892                0.001489               0.998464         REFUTES   
18893                0.001489               0.998464         REFUTES   
18894                0.001489               0.998464         REFUTES   
18895                0.001489               0.998464         REFUTES   

       score_on_predicted_label  
0                      

In [73]:
# describe() of evidence of type claim
tdf = explanation_df[explanation_df['type'] == 'claim_intercept']
tdf.groupby('predicted_label')['score_on_predicted_label'].describe()

count      mean       std       min       25%       50%  \
predicted_label                                                             
REFUTES          1620.0  0.913685  0.178692 -0.216809  0.919250  0.992907   
SUPPORTS         1387.0  0.269326  0.390558 -0.524601 -0.030526  0.257804   

                      75%       max  
predicted_label                      
REFUTES          0.997837  1.408975  
SUPPORTS         0.558571  1.089270

## Discussion

In [74]:
# plot the distribution of score_on_predicted_label kde estimation and histogram curve
fig = px.histogram(explanation_df, x='score_on_predicted_label', histnorm='percent',
                   title='Histogram of score_on_predicted_label',
                   labels={'score_on_predicted_label': 'score_on_predicted_label', 'value': 'percentage'},
                   )
fig.show()

# the same plot segmented by predicted_label
fig = px.histogram(explanation_df, x='score_on_predicted_label', histnorm='percent',
                   title='Histogram of score_on_predicted_label',
                   labels={'score_on_predicted_label': 'score_on_predicted_label', 'value': 'percentage'},
                   color='predicted_label'
                   )
fig.show()


## Discussion

# Understand the distribution of importance over the evidence set.
    1. Is the model focusing on a small subset or distributing the impacts evenly?

In [75]:
tdf

id             type  \
1       4329  claim_intercept   
4       5003  claim_intercept   
11      6079  claim_intercept   
18      6473  claim_intercept   
43      8406  claim_intercept   
...      ...              ...   
18880  51676  claim_intercept   
18883  52200  claim_intercept   
18887  52212  claim_intercept   
18890  52216  claim_intercept   
18894  52288  claim_intercept   

                                               unit_text  unit_index  \
1      George Brown began his Liberal Party leadershi...           0   
4      Brookings University Residential Historic Dist...           0   
11     After his brother died from a drug overdose, A...           0   
18     Sajana Raina was gifted a Yamaha scooter when ...           0   
43     Jean Michaël Seri only play at local football ...           0   
...                                                  ...         ...   
18880                                                NaN           0   
18883                                                NaN           0   
18887                                                NaN           0   
18890                                                NaN           0   
18894                                                NaN           0   

       SUPPORTS   REFUTES  NOT ENOUGH INFO        filename  num_samples  \
1      0.002052  0.997914         0.000034        ex_AB_00          NaN   
4      0.004898  0.995047         0.000054        ex_AB_00          NaN   
11    -0.058798  1.058721         0.000077        ex_AB_00          NaN   
18     0.484786  0.515111         0.000103        ex_AB_00          NaN   
43     0.001729  0.998242         0.000029        ex_AB_00          NaN   
...         ...       ...              ...             ...          ...   
18880  0.470916  0.528973         0.000111  original_TO_01        500.0   
18883  0.003205  0.996756         0.000039  original_TO_01        500.0   
18887  0.003943  0.995988         0.000069  original_TO_01        500.0   
18890  0.001881  0.998076         0.000042  original_TO_01        500.0   
18894  0.009885  0.990028         0.000087  original_TO_01        500.0   

          label  execution_time  local_pred  NOT ENOUGH INFO_predict_proba  \
1           NaN             NaN    0.998062                       0.000033   
4           NaN             NaN    0.995205                       0.000054   
11          NaN             NaN    0.353855                       0.000047   
18          NaN             NaN    0.101297                       0.000055   
43          NaN             NaN    0.998447                       0.000028   
...         ...             ...         ...                            ...   
18880  SUPPORTS        6.308749   -0.240132                       0.000088   
18883   REFUTES        6.265906    0.996751                       0.000039   
18887   REFUTES        6.314912    0.998295                       0.000038   
18890   REFUTES        7.933691    0.998437                       0.000044   
18894   REFUTES        6.628436    0.994046                       0.000048   

       SUPPORTS_predict_proba  REFUTES_predict_proba predicted_label  \
1                    0.001757               0.998210         REFUTES   
4                    0.004583               0.995363         REFUTES   
11                   0.992824               0.007130        SUPPORTS   
18                   0.993240               0.006705        SUPPORTS   
43                   0.001541               0.998431         REFUTES   
...                       ...                    ...             ...   
18880                0.998814               0.001098        SUPPORTS   
18883                0.003215               0.996746         REFUTES   
18887                0.001192               0.998770         REFUTES   
18890                0.001158               0.998798         REFUTES   
18894                0.001489               0.998464         REFUTES   

       score_on_predicted_label  
1          

In [76]:
only_evidence_mask = explanation_df['type'] == 'evidence'
tdf = explanation_df[only_evidence_mask].copy()
# cut evidence with less than 10 samples
# tdf = tdf.groupby('unit_index').filter(lambda x: len(x) > 10)
tdf['score_percentage'] = tdf['score_on_predicted_label'] / tdf.groupby(id_cols)['score_on_predicted_label'].transform(
    'sum') * 100

# sort impact id_cols and score_on_predicted_label
tdf.sort_values(by=id_cols + ['score_on_predicted_label'], ascending=False, inplace=True)
# cumulative sum starting from the highest score_percentage by id
tdf['cumsum_score_percentage'] = tdf.groupby(id_cols)['score_percentage'].transform('cumsum')
# save the ordered index of the score_percentage
tdf['rank_score'] = tdf.groupby(id_cols)['score_on_predicted_label'].transform(
    lambda x: x.rank(ascending=False, method='first'))

# group by rank_score and calculate the mean, std and confindence interval of the score_percentage
grouped_df = tdf.groupby('rank_score')['score_on_predicted_label'].agg(
    ['mean', 'std', ('mean_ci', xfc.xfc_utils.mean_confidence_interval)]).reset_index()

fig = go.Figure()
# add a line for each predicted_label
for tpredicted_label in tdf['predicted_label'].unique():
    # filter the predicted_label
    tdf_predicted = tdf[tdf['predicted_label'] == tpredicted_label]
    # add line with the mean of the score_on_predicted_label
    tgroup_df = tdf_predicted.groupby('rank_score')['score_on_predicted_label'].agg(
        ['mean', 'std', ('mean_ci', xfc.xfc_utils.mean_confidence_interval)]).reset_index()
    # add the equivalent with std
    fig.add_trace(go.Scatter(
        x=tgroup_df['rank_score'],
        y=tgroup_df['mean'],
        error_y=dict(
            type='data',
            array=tgroup_df['std'],
            visible=True
        ),
        mode='lines',
        name=tpredicted_label+ '_std'
    ))
    # then add the line with mean_ci
    fig.add_trace(go.Scatter(
        x=tgroup_df['rank_score'],
        y=tgroup_df['mean'],
        error_y=dict(
            type='data',
            array=tgroup_df['mean_ci'],
            visible=True
        ),
        mode='lines',
        name=tpredicted_label+ '_ci'
    ))
fig.update_layout(title='score_on_predicted_label over the ranked evidence (mean, std)',
                  **layout_dict, **h_legend_dict)
fig.show()
# save_fig(fig, '02-score_on_predicted_label_ranked_evidence')

# plot the mean and std of cumulative sum of the score_percentage
# grouped_df = tdf.groupby('rank_score')['score_percentage'].agg(
#     ['mean', 'std', ('mean_ci', xfc.xfc_utils.mean_confidence_interval)]).reset_index()
# fig = px.line(grouped_df, x='rank_score', y='mean', title='score_percentage over the ranked evidence (mean, std)',
#               labels={'rank_score': 'rank_score', 'mean': 'mean'},
#               error_y='std'
#               )
# fig.show()
# save_fig(fig, '02-score_percentage_ranked_evidence')

# same chart replicated for each filename
for filename in tdf['filename'].unique():
    fig = go.Figure()
    for tpredicted_label in tdf['predicted_label'].unique():
        # filter the predicted_label
        tdf_predicted = tdf[(tdf['predicted_label'] == tpredicted_label) & (tdf['filename'] == filename)]        
        # add line with the mean of the score_on_predicted_label
        tgroup_df = tdf_predicted.groupby('rank_score')['score_on_predicted_label'].agg(
            ['mean', 'std', ('mean_ci', xfc.xfc_utils.mean_confidence_interval)]).reset_index()
        # add the equivalent with std        
        fig.add_trace(go.Scatter(
            x=tgroup_df['rank_score'],
            y=tgroup_df['mean'],
            error_y=dict(
                type='data',
                array=tgroup_df['std'],
                visible=True
            ),
            mode='lines',
            name=tpredicted_label + '_std'
        ))
        # then add the line with mean_ci
        fig.add_trace(go.Scatter(
            x=tgroup_df['rank_score'],
            y=tgroup_df['mean'],
            error_y=dict(
                type='data',
                array=tgroup_df['mean_ci'],
                visible=True
            ),
            mode='lines',
            name=tpredicted_label + '_ci'
        ))
    fig.update_layout(title=f'{filename} score_on_predicted_label over the ranked evidence (mean, std)',
                      **layout_dict, **h_legend_dict)
    # save_fig(fig, f'02-{filename}_score_on_predicted_label_ranked_evidence')
    fig.show()


/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide



/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide



/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide



/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide



/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:269: RuntimeWarning:

Degrees of freedom <= 0 for slice

/home/bussotti/.conda/envs/feverous2/lib/python3.10/site-packages/numpy/core/_methods.py:261: RuntimeWarning:

invalid value encountered in scalar divide

